# Lending Clug Case Study: Credit Risk
description...

## Imports & Settings

In [1]:
import pandas as pd
import plotly.io as pio
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import numpy as np

pd.options.plotting.backend = "plotly"


In [2]:
# for better visibility, we will display the whole dataframe and show floats with 2 decimal places
pd.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.2f' % x)

# set the renderer to display plots in VSCode
pio.renderers.default = "notebook_connected"


## First Look

In [3]:
df = pd.read_csv('loan.csv')
df.set_index('id', inplace=True)
df.head(5)


/Users/houghton/opt/anaconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3444: DtypeWarning:

Columns (47) have mixed types.Specify dtype option on import or set low_memory=False.



member_id  loan_amnt  funded_amnt  funded_amnt_inv        term  \
id                                                                        
1077501    1296599       5000         5000          4975.00   36 months   
1077430    1314167       2500         2500          2500.00   60 months   
1077175    1313524       2400         2400          2400.00   36 months   
1076863    1277178      10000        10000         10000.00   36 months   
1075358    1311748       3000         3000          3000.00   60 months   

        int_rate  installment grade sub_grade                 emp_title  \
id                                                                        
1077501   10.65%       162.87     B        B2                       NaN   
1077430   15.27%        59.83     C        C4                     Ryder   
1077175   15.96%        84.33     C        C5                       NaN   
1076863   13.49%       339.31     C        C1       AIR RESOURCES BOARD   
1075358   12.69%        67.79     B        B5  University Medical Group   

        emp_length home_ownership  annual_inc verification_status issue_d  \
id                                                                          
1077501  10+ years           RENT    24000.00            Verified  Dec-11   
1077430   < 1 year           RENT    30000.00     Source Verified  Dec-11   
1077175  10+ years           RENT    12252.00        Not Verified  Dec-11   
1076863  10+ years           RENT    49200.00     Source Verified  Dec-11   
1075358     1 year           RENT    80000.00     Source Verified  Dec-11   

         loan_status pymnt_plan  \
id                                
1077501   Fully Paid          n   
1077430  Charged Off          n   
1077175   Fully Paid          n   
1076863   Fully Paid          n   
1075358      Current          n   

                                                       url  \
id                                                           
1077501  https://lendingclub.com/browse/loanDetail.acti...   
1077430  https://lendingclub.com/browse/loanDetail.acti...   
1077175  https://lendingclub.com/browse/loanDetail.acti...   
1076863  https://lendingclub.com/browse/loanDetail.acti...   
1075358  https://lendingclub.com/browse/loanDetail.acti...   

                                                      desc         purpose  \
id                                                                           
1077501    Borrower added on 12/22/11 > I need to upgra...     credit_card   
1077430    Borrower added on 12/22/11 > I plan to use t...             car   
1077175                                                NaN  small_business   
1076863    Borrower added on 12/21/11 > to pay for prop...           other   
1075358    Borrower added on 12/21/11 > I plan on combi...           other   

                        title zip_code addr_state   dti  delinq_2yrs  \
id                                                                     
1077501              Computer    860xx         AZ 27.65            0   
1077430                  bike    309xx         GA  1.00            0   
1077175  real estate business    606xx         IL  8.72            0   
1076863              personel    917xx         CA 20.00            0   
1075358              Personal    972xx         OR 17.94            0   

        earliest_cr_line  inq_last_6mths  mths_since_last_delinq  \
id                                                                 
1077501           Jan-85               1                     NaN   
1077430           Apr-99               5                     NaN   
1077175           Nov-01               2                     NaN   
1076863           Feb-96               1                   35.00   
1075358           Jan-96               0                   38.00   

         mths_since_last_record  open_acc  pub_rec  revol_bal revol_util  \
id                                                                         
1077501                     NaN         3        0     

## Data Dictionary

In [4]:
# For easy access we can create a dataframe with the descriptions from the accompanying Data_Dictionary.xlsx

data_dict = pd.read_excel('Data_Dictionary.xlsx',
                          index_col=0, header=None).iloc[:, 0:1].transpose()

# the last two columns don't contain descriptions, so we will drop them
data_dict = data_dict.drop(columns=np.nan)
data_dict

KeyError: '[nan] not found in axis'

@Krilecy I'm not quite sure why this is throwing an error now when it wasn't earlier 🤔

## Data Clean Up

While importing, Pandas already warns us that there are columns with mixed data types. 
> 'DtypeWarning: Columns (47) have mixed types.'

For the analysis we need our data to be correctly formatted (preferably numeric).

### Empty & Monotonous Columns
If the data contains completely empty columns we can drop them as they don't contain any information to analyze.

In [5]:
empty_cols = [col for col in df.columns if df[col].isnull().all()]
print(len(empty_cols), 'empty columns found')
print('Empty columns:', empty_cols)

df.drop(empty_cols, axis=1, inplace=True)


54 empty columns found
Empty columns: ['mths_since_last_major_derog', 'annual_inc_joint', 'dti_joint', 'verification_status_joint', 'tot_coll_amt', 'tot_cur_bal', 'open_acc_6m', 'open_il_6m', 'open_il_12m', 'open_il_24m', 'mths_since_rcnt_il', 'total_bal_il', 'il_util', 'open_rv_12m', 'open_rv_24m', 'max_bal_bc', 'all_util', 'total_rev_hi_lim', 'inq_fi', 'total_cu_tl', 'inq_last_12m', 'acc_open_past_24mths', 'avg_cur_bal', 'bc_open_to_buy', 'bc_util', 'mo_sin_old_il_acct', 'mo_sin_old_rev_tl_op', 'mo_sin_rcnt_rev_tl_op', 'mo_sin_rcnt_tl', 'mort_acc', 'mths_since_recent_bc', 'mths_since_recent_bc_dlq', 'mths_since_recent_inq', 'mths_since_recent_revol_delinq', 'num_accts_ever_120_pd', 'num_actv_bc_tl', 'num_actv_rev_tl', 'num_bc_sats', 'num_bc_tl', 'num_il_tl', 'num_op_rev_tl', 'num_rev_accts', 'num_rev_tl_bal_gt_0', 'num_sats', 'num_tl_120dpd_2m', 'num_tl_30dpd', 'num_tl_90g_dpd_24m', 'num_tl_op_past_12m', 'pct_tl_nvr_dlq', 'percent_bc_gt_75', 'tot_hi_cred_lim', 'total_bal_ex_mort', 't

In [6]:
# reviewing distribution of null values in columns

col_null_values = df.isnull().sum()
col_null_values.hist(nbins=20)


Columns that contain nothing but one value don't add any information and can be droped. We also look at columns with 2 values to see if they can be dropped.

In [7]:
# dropping columns with single unique values
cols_with_1_value = [col for col in df.columns if df[col].nunique() == 1]
df.drop(cols_with_1_value, axis=1, inplace=True)


In [8]:
# dropping columns with two unique values
cols_with_2_values = [col for col in df.columns if df[col].nunique() == 2]
for col in cols_with_2_values:
    print(col, df[col].unique())


term [' 36 months' ' 60 months']
next_pymnt_d [nan 'Jun-16' 'Jul-16']


In [9]:
df.next_pymnt_d.value_counts()


Jun-16    1125
Jul-16      15
Name: next_pymnt_d, dtype: int64

Just the 'term' (duration of the loan) (36 or 60 months) and the 'next_pymnt_d' (June or July 2016 if any) have only 2 different values. 
<br>Duration might be a factor associated with credit risk, so we leave that column in.
<br>We assume that the cut-off date was in or before June 2016, so that the entries in 'next_pymnt_d' were in the future when the data was taken. This would explain why there are so few and it fits with the time frame of the project description 
(2011 + 60 months = 2017). We don't know if these payments happened but might need the information and therefor leave the column in.

In [10]:
# Since we are interested in finding predictors for default risk a.k.a. the 'loan_status' column, we can drop the currently active contracts as we don't know their outcome.

df = df[df['loan_status'] != 'Current']

# We can also check for null values in the loan status column.
df['loan_status'].isnull().sum()


0

### Units

We can convert units that are spelled out in each cell to numeric values

In [11]:
# converting all columns with units in in values to numbers
df['term'] = df['term'].str.replace(' months', '').astype(int)
df.rename(columns={'term': 'term_in_months'}, inplace=True)

df['int_rate'] = df['int_rate'].str.replace('%', '').astype(float)
df['revol_util'] = df['revol_util'].str.replace('%', '').astype(float)


In [12]:
df.emp_length.unique()


array(['10+ years', '< 1 year', '3 years', '8 years', '9 years',
       '4 years', '5 years', '1 year', '6 years', '2 years', '7 years',
       nan], dtype=object)

We see above that the employment length has 3 vaules (<1,1 and 10+) that don't end in 'years'. We can convert these.


In [13]:
df['emp_length'] = df['emp_length'].replace('10+ years', 10).astype(str)
df['emp_length'] = df['emp_length'].replace('< 1 year', 0.5).astype(str)
df['emp_length'] = df['emp_length'].replace('1 year',     1).astype(str)

df['emp_length'] = df['emp_length'].str.replace(' years', '').astype(float)


### Dates

In [14]:
# Looking at the table we can see the following columns contain dates
cols_with_date = [
    'issue_d', 'earliest_cr_line',
    'last_pymnt_d', 'next_pymnt_d',
    'last_credit_pull_d'
]

for col in cols_with_date:
    df[col] = pd.to_datetime(df[col], format='%b-%y')


### Zip Codes
We can use the provided first 3 digits of ZIP codes to identify any (rough) geographic pattern.

In [15]:
df.zip_code = df.zip_code.str.replace('xx', '')
df.zip_code.value_counts()

100    583
945    531
112    502
606    493
070    455
      ... 
463      1
381      1
592      1
414      1
469      1
Name: zip_code, Length: 822, dtype: int64

### Description Column

The description column ('desc') contains unstructured data. Let's see if we can extract usefull information from it.

In [16]:
print(len(df.desc.unique()), 'unique descriptions')

print('Examples:')
for desc in df.sample(5).desc:
    print('-', str(desc).strip())


25804 unique descriptions
Examples:
- nan
- Requesting a loan to help consolidate my bills into one low monthly payment. Thanks for looking!
- Borrower added on 03/09/11 > I plan to use the funds to consolidate all of my credit card debt into one loan. That way I'll have a set payoff date, regular monthly payments and I'll be able to start saving money at the same time! <br/><br/>I care very much about my credit and always pay all my bills on time. I've never missed a payment or ever been late! <br/><br/>My job is very stable as I'm an accountant and have been working at the same company for the last 6 years.<br/><br/>I'm currently paying $906 a month towards my credit cards. With this loan, I'll save $516.74 of that amount and be able to put it into a savings account!<br/>
- Borrower added on 09/03/11 > Dear Lenders:<br/><br/>I have listed this personal loan and I&rsquo;d like to answer the four important questions as follows:<br/><br/>How do I plan to use the funds:<br/> - The funds 

The descriptions often contain the date when the borrower was added and their usecase. Although the usecase might be interesting for further analysis we only extract the date so we can use it in the bivariate analysis later.

In [17]:
df['desc'].values

array(['  Borrower added on 12/22/11 > I need to upgrade my business technologies.<br>',
       '  Borrower added on 12/22/11 > I plan to use this money to finance the motorcycle i am looking at. I plan to have it paid off as soon as possible/when i sell my old bike. I only need this money because the deal im looking at is to good to pass up.<br><br>  Borrower added on 12/22/11 > I plan to use this money to finance the motorcycle i am looking at. I plan to have it paid off as soon as possible/when i sell my old bike.I only need this money because the deal im looking at is to good to pass up. I have finished college with an associates degree in business and its takingmeplaces<br>',
       nan, ..., nan, nan,
       'I plan to consolidate over $7,000 of debt: a combination of credit cards and student loans.'],
      dtype=object)

In [18]:
# extract the date from the description if the description starts with 'Borrower added on'
def extract_added_date(desc):
    desc = str(desc).strip()
    if desc.startswith('Borrower added on'):
        return desc.split(' >')[0][-8:]
    else:
        return None


# insert the new column next to the description column and convert it to datetime
df.insert(df.columns.get_loc('desc') + 1, 'borrower_added_d',
          df.desc.apply(extract_added_date))
df['borrower_added_d'] = pd.to_datetime(
    df['borrower_added_d'], format='%m/%d/%y', errors='coerce')


In [19]:
# The web addresses of the URL column are inaccessible and therefore beyond the scope of this assignment.
df.drop(['url'], axis=1, inplace=True)


### Grades

In [20]:
# Converting the sub_grade scale to categorical numerical values

df['grade_num'] = df.sub_grade.astype("category").cat.codes
df['grade_num'].value_counts()

# We can drop the grade and sub_grade column as it is no longer needed.
df.drop(['sub_grade', 'grade'], axis=1, inplace=True)

### Excluding with Data Dict
With the description of the column content we can dop more columns


In [21]:
# Create one set with column names that are in both the DF and Data Dictionary

cols_from_both = list(set(df.columns).intersection(set(data_dict.columns)))


pd.set_option('display.max_colwidth', None)

#Display the columns and their descriptions from the Data Dictionary
data_dict.transpose().loc[cols_from_both].style.set_properties(
    **{'text-align': 'left'})


In [22]:
pd.reset_option('display.max_colwidth')


From the displayed list of descriptions above we can exclude some of the columns that are irrelevant to the analysis.

In [23]:
# As we try to predict the loan status before the loan is given, we can drop the columns that show information about events occurring during the loan period or after the customer has already defaulted.
cols_to_drop = ['collection_recovery_fee','total_rec_late_fee', 'last_pymnt_d']

# We excluded ongoing loans and can therefore drop the following columns
cols_to_drop = cols_to_drop + ['out_prncp','total_pymnt','out_prncp_inv','total_rec_int','last_pymnt_amnt','next_pymnt_d', 'total_rec_prncp', 'funded_amnt_inv']


print(f'These {len(cols_to_drop)} columns will be dropped:')
print(cols_to_drop)

These 11 columns will be dropped:
['collection_recovery_fee', 'total_rec_late_fee', 'last_pymnt_d', 'out_prncp', 'total_pymnt', 'out_prncp_inv', 'total_rec_int', 'last_pymnt_amnt', 'next_pymnt_d', 'total_rec_prncp', 'funded_amnt_inv']


In [24]:
df.drop(cols_to_drop, axis=1, inplace=True)

## Derived Metrics

### Ratio of income to emplyoment length
As the ratio of income to emplyoment length goes up and down, do we see a difference in the number of charged off accounts?

In [25]:
df['annual_inc'].plot.box()

It's evident that there are some outliers in the income featureset. We can drop rows that are outside the upper fence.

In [82]:
df.drop(df.index[df['annual_inc'] > 200000], inplace=True)

In [83]:
df['annual_inc'].plot.box()

The distribution looks much cleaner now. Now we're ready to create a new derived metric to understand the relationship between and expertise (a combination between income and employment length) an loan_status.

In [28]:
df['quality_of_expertise'] = df['annual_inc'] / df['emp_length']

In [29]:
# We'll go ahead and do min-max normalization on the quality of expertise column to allow us us to get a better read on this variable over time.
df['quality_of_expertise_norm'] =(df['quality_of_expertise']-df['quality_of_expertise'].min())/(df['quality_of_expertise'].max()-df['quality_of_expertise'].min())

In [30]:
fig = go.Figure(data=go.Scatter(x=df['loan_status'],
                                y=df['quality_of_expertise_norm'],
                                mode='markers',
                                marker=dict(
                                    size=5,
                                    color=np.random.randn(500), #set color equal to a variable
                                    colorscale='Viridis', # one of plotly colorscales
                                    showscale=True
    )))

fig.show()

We can see from the graph above that the concetration of 'Charged Off' accounts lessons as the quality of expertise goes up.

## Overview

In [31]:
df.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 38007 entries, 1077501 to 87023
Data columns (total 37 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   member_id                  38007 non-null  int64         
 1   loan_amnt                  38007 non-null  int64         
 2   funded_amnt                38007 non-null  int64         
 3   term_in_months             38007 non-null  int64         
 4   int_rate                   38007 non-null  float64       
 5   installment                38007 non-null  float64       
 6   emp_title                  35682 non-null  object        
 7   emp_length                 36982 non-null  float64       
 8   home_ownership             38007 non-null  object        
 9   annual_inc                 38007 non-null  float64       
 10  verification_status        38007 non-null  object        
 11  issue_d                    38007 non-null  datetime64[ns]
 12

In [32]:
df.describe()


member_id  loan_amnt  funded_amnt  term_in_months  int_rate  \
count   38007.00   38007.00     38007.00        38007.00  38007.00   
mean   842415.60   10924.35     10667.34           41.88     11.91   
std    264439.91    7238.28      6985.31           10.32      3.68   
min     70699.00     500.00       500.00           36.00      5.42   
25%    661448.00    5200.00      5000.00           36.00      8.94   
50%    839297.00    9600.00      9325.00           36.00     11.71   
75%   1037338.50   15000.00     15000.00           36.00     14.35   
max   1314167.00   35000.00     35000.00           60.00     24.40   

       installment  emp_length  annual_inc      dti  delinq_2yrs  \
count     38007.00    36982.00    38007.00 38007.00     38007.00   
mean        318.81        4.99    64583.11    13.35         0.15   
std         204.96        3.47    33619.58     6.66         0.49   
min          15.69        0.50     4000.00     0.00         0.00   
25%         164.90        2.00    40000.00     8.22         0.00   
50%         275.81        4.00    58000.00    13.45         0.00   
75%         419.82        9.00    80000.00    18.62         0.00   
max        1305.19       10.00   200000.00    29.99        11.00   

       inq_last_6mths  mths_since_last_delinq  mths_since_last_record  \
count        38007.00                13444.00                 2713.00   
mean             0.87                   35.94                   69.51   
std              1.07                   22.04                   43.90   
min              0.00                    0.00                    0.00   
25%              0.00                   18.00                   21.00   
50%              1.00                   34.00                   90.00   
75%              1.00                   52.00                  104.00   
max              8.00                  120.00                  129.00   

       open_acc  pub_rec  revol_bal  revol_util  total_acc  total_pymnt_inv  \
count  38007.00 38007.00   38007.00    37958.00   38007.00         38007.00   
mean       9.25     0.06   12952.59       48.67      21.93         11133.82   
std        4.39     0.24   15144.89       28.33      11.36          8551.81   
min        2.00     0.00       0.00        0.00       2.00             0.00   
25%        6.00     0.00    3624.50       25.20      13.00          4982.39   
50%        9.00     0.00    8674.00       49.10      20.00          8976.46   
75%       12.00     0.00   16652.00       72.20      29.00         15139.20   
max       44.00     4.00  149588.00       99.90      90.00         58563.68   

       recoveries  pub_rec_bankruptcies  grade_num  quality_of_expertise  \
count    38007.00              37324.00   38007.00              36982.00   
mean        97.49                  0.04       9.78              30474.57   
std        695.18                  0.21       6.74              43754.71   
min          0.00                  0.00       0.00                808.80   
25%          0.00                  0.00       4.00               7714.29   
50%          0.00                  0.00       9.00              13760.50   
75%          0.00                  0.00      14.00              31200.00   
max      29623.35                  2.00      34.00             400000.00   

       quality_of_expertise_norm  
count                   36982.00  
mean                        0.07  
std                         0.11  
min                         0.00  
25%                         0.02  
50%                         0.03  
75%                         0.08  
max                         1.00

Now that we've done some cleaning up of the data, we can begin to explore and understand different feature at length and its surface level impact to loan _status. We'll start with features we feel could be valuable indicators of correlation to loan_status.

## Feature Analysis

### Function Definitions

In [33]:
def plot_distribution(column_name):
    """ Plots feature value distribution in both Violin and Box plot formats. """

    fig = make_subplots(rows=2, cols=1)

    fig.add_trace(
        go.Violin(x=df[column_name], name="Violin plot"),
        row=1, col=1
    )

    fig.add_trace(
        go.Box(x=df[column_name], name="Box plot"),
        row=2, col=1
    )

    fig.update_layout(height=600, width=800,
                      title_text=f"Distribution of '{column_name}' values")
    fig.show()

    return


In [34]:
def plot_surface_impact(column_name):
    """ Plots loan_status' impact to N feature's mean, median, max and min values. """

    fig = make_subplots(rows=4, cols=1)

    variable_impact = pd.DataFrame()
    variable_impact['mean_impact'] = df.groupby(['loan_status'])[
        column_name].mean()
    variable_impact['median_impact'] = df.groupby(
        ['loan_status'])[column_name].median()
    variable_impact['max_impact'] = df.groupby(['loan_status'])[
        column_name].max()
    variable_impact['min_impact'] = df.groupby(['loan_status'])[
        column_name].min()

    fig.add_trace(
        go.Bar(y=variable_impact['mean_impact'],
               x=variable_impact.index, name="Impact to mean"),
        row=1, col=1
    )

    fig.add_trace(
        go.Bar(y=variable_impact['median_impact'],
               x=variable_impact.index, name="Impact to median"),
        row=2, col=1
    )

    fig.add_trace(
        go.Bar(y=variable_impact['max_impact'],
               x=variable_impact.index, name="Impact to max"),
        row=3, col=1
    )

    fig.add_trace(
        go.Bar(y=variable_impact['min_impact'],
               x=variable_impact.index, name="Impact to min"),
        row=4, col=1
    )

    fig.update_layout(height=600, width=800,
                      title_text=f"Impact of '{column_name}' on surface statistics of 'loan_status' values")
    fig.show()

    return


In [35]:
def get_default_rate(col_name, min_count=30):
    """ Returns the rate at which customers that defaulted on the loan for each unique value in the passed column. Minimum Count is the minimum number of customers that must have the value in order to be included in the calculation. """

    default_rate = {}

    for val in df[col_name].unique():

        total = len(df.loc[df[col_name] == val])
        if total >= min_count:
            defaults = len(df.loc[(df[col_name] == val) & (df['loan_status'] == 'Charged Off')])
            default_rate[val] = defaults / total

    return default_rate


In [36]:
def plot_from_dict(dict):
    """ Plots a bar chart from a dictionary. """

    df = pd.DataFrame.from_dict(dict, orient='index')
    df.sort_values(by=0, inplace=True, ascending=False)
    plt = df.plot(kind='bar')
    plt.show()

### Feature Plots

To visualize the data we can plot a number of selected variables to get impression of their distribution.

In [37]:
plot_distribution('loan_amnt')
plot_surface_impact('loan_amnt')

plot_distribution('funded_amnt')
plot_surface_impact('funded_amnt')

plot_distribution('dti')
plot_surface_impact('dti')

plot_surface_impact('term_in_months')

plot_distribution('int_rate')
plot_surface_impact('int_rate')


### Anual income (binned)

In [138]:
highest_income = df[df['annual_inc'].between(80000, 140000)]
midtier_income = df[df['annual_inc'].between(58000, 80000)]
low_income = df[df['annual_inc'].between(40000, 58000)]

In [135]:
highest_income['loan_status_num'].mean()

0.8848896044158233

In [137]:
midtier_income['loan_status_num'].mean()

0.8581552892131319

In [136]:
low_income['loan_status_num'].mean()

0.8478029937228392

By binning annual income into 3 chunks we're cleanly able to see that the mean loan status is greater for high income individuals. Remember the loan_status_num column represents loan_status in the form of 0 and 1. The greater than 'Fully paid' loans there are the more 1's we'll see in the data. As we see more ones, the mean will go up.

### Summary of initial distribution findings

- The mean and min loan amount for accounts "Charged Off" are slightly higher than accounts that were 'Fully Paid'
- The debt to income ratio is higher for accounts that were 'Charged Off' than accounts that were 'Fully Paid'
- The loan term was several months longer on average for 'Charged Off' accounts than loan terms for 'Fully Paid' accounts.
- Mean interest rates were higher for 'Charged Off' accounts than 'Fully Paid' accounts.
- As expected, the mean and max late fee values for 'Charged Off' accounts were much higher than 'Fully Paid' accounts.

Secondary lessons:
- While the mean may have shifted the max and min values remain rather constant. In order to account for this skewed distribution in our analysis, we also looked at the median of the feature, illustrated in the red bar charts above.
- Debt to income and interest rate appear to have slightly higher median values for 'Charged Off' accounts compared to 'Fully Paid' accounts.

### Correlation Matrix

In [38]:
df['loan_status_num'] = df.loan_status.astype("category").cat.codes

In [39]:

# Generate correlation matrix
df_corr = df.corr() 


# Plot heatmap of correlation matrix
fig = go.Figure()
fig.add_trace(
    go.Heatmap(
        x=df_corr.columns,
        y=df_corr.columns,
        z=np.array(df_corr)
    )
)
fig.update_layout(height=1000, width=1000)
fig.show()


## Geo Data

In [40]:
default_rate_by_state = get_default_rate('addr_state')
default_rate_by_zip = get_default_rate('zip_code')

In [41]:
plot_from_dict(default_rate_by_state)

While we do see a gradual distribution of interest rates by states, its worthwhile to note that the delta between Nevada and South Dakota is much larger than the delta between other US states. When evaluating loan applications, predicting 'Charge Offs before they happen will most likely need to take into consideration state or region.

In [42]:
plot_from_dict(default_rate_by_zip)

## Purchases
We can check if the purpose of the loan has any bearing on the default rate.

In [43]:
default_rate_by_purpose = get_default_rate('purpose')

plot_from_dict(default_rate_by_purpose)

For the reportet spending categories we see a significant higher default rate for small businesses. Because we know that interest rates were higher for accounts that ultimately had a status of 'Charged Off', this would present as a feature of interest for lending companies looking to be more cautious with their loan approvals.

## Number of public bankruptcies 
We can check if the number of public bankrupcies has any bearing on the default interest rate. We expect it should.


In [44]:
default_rate_by_purpose = get_default_rate('pub_rec_bankruptcies')

plot_from_dict(default_rate_by_purpose)

As expected, if you have even a single public bankruptcy, you end up with a higher the interest rate. Almost twice the size.

### Next steps
- ☑️ Purchases analysis
- ☑️ Zip code analysis
- ☑️ Reduce number of features that are not needed (post 'Charge Off' status)
- Derived metrics (description)
- Normalize continuous variables



### Last steps
- Creation of slides